# Actividad: Entornos Multiagentes

**Integrantes:**
- Karla González Sánchez A01541526
- Luis Ángel Alba Alfaro A01640314
- María Fernanda Elizalde Macías A01634135
- Sofía del Pilar Batiz Martínez A01634125

Modelación de sistemas multiagentes con gráficas computacionales  
Gamaliel Abisay Palomo Briones  
Omar Mendoza Montoya  
Guillermo Gabriel Rivas Aguilar  
14 de noviembre de 2022  

Importar librerías

In [20]:
import agentpy as ap

## Problema 1

## Problema 2

In [21]:
import matplotlib.pyplot as plt
import seaborn as sns
import IPython
import random

Definicion del modelo

In [22]:
class ForestModel(ap.Model):

    def setup(self):

        # Create agents (trees)
        n_trees = int(self.p['Tree density'] * (self.p.size**2)) #numero de arboles
        trees = self.agents = ap.AgentList(self, n_trees)

        # Create grid (forest)
        self.forest = ap.Grid(self, [self.p.size]*2, track_empty=True)
        self.forest.add_agents(trees, random=True, empty=True)

        # Initiate a dynamic variable for all trees
        # Condition 0: Alive, 1: Burning, 2: Burned
        self.agents.condition = 0

        # Start a fire from the left side of the grid
        randX = random.randint(1, self.p.size - 1)
        randY = random.randint(1, self.p.size - 1)
        unfortunate_trees = self.forest.agents[randX:randX + 5, randY:randY + 5]
        unfortunate_trees.condition = 1

    def step(self):

        # Select burning trees
        burning_trees = self.agents.select(self.agents.condition == 1)

        # Spread fire
        for tree in burning_trees:
            for neighbor in self.forest.neighbors(tree):
                if neighbor.condition == 0:
                    neighbor.condition = 1 # Neighbor starts burning
            tree.condition = 2 # Tree burns out

        # Stop simulation if no fire is left
        if len(burning_trees) == 0:
            self.stop()

    def end(self):

        # Document a measure at the end of the simulation
        burned_trees = len(self.agents.select(self.agents.condition == 2))
        self.report('Percentage of burned trees',
                    burned_trees / len(self.agents))

Animacion

In [23]:
parameters = {
    'Tree density': 0.6, # Percentage of grid covered by trees
    'size': 50, # Height and length of the grid
    'steps': 100,
}

In [24]:
def animation_plot(model, ax):
    attr_grid = model.forest.attr_grid('condition')
    color_dict = {0:'#7FC97F', 1:'#d62c2c', 2:'#e5e5e5', None:'#d5e5d5'}
    ap.gridplot(attr_grid, ax=ax, color_dict=color_dict, convert=True)
    ax.set_title(f"Simulation of a forest fire\n"
                 f"Time-step: {model.t}, Trees left: "
                 f"{len(model.agents.select(model.agents.condition == 0))}")

fig, ax = plt.subplots()
model = ForestModel(parameters)
animation = ap.animate(model, fig, ax, animation_plot)
IPython.display.HTML(animation.to_jshtml(fps=15))

## Problema 3

In [37]:
import agentpy as ap
import random
import matplotlib.pyplot as plt
import seaborn as sns
import IPython

Definir las coordenadas de los posibles movimientos:

In [38]:
moves = [
    (-1,-1),(-1,0),(-1,1),
    (0,-1),(0,1),(0,0),
    (1,-1),(1,1),(1,0),
]

Definición del modelo

In [64]:
class VacuumModel(ap.Model):

    def setup(self):
        
        #Crear agentes
        n_trash = int((self.p['density'] * self.p.height * self.p.length))
        self.trash = self.agents = ap.AgentList(self, n_trash)
        self.robots = ap.AgentList(self, self.p['Number of robots'])

        #Grid
        self.area = ap.Grid(self, (self.p.height, self.p.length), track_empty=True)
        self.area.add_agents(self.trash, random="True", empty="True")

        #Agregar agentes
        self.area.add_agents(self.robots, random=True, empty=False)

        #Condiciones de los robots
        # 0 -> Sucio, 1 -> Robot, 2 -> Limpio
        self.trash.condition = 0
        self.robots.condition = 1


    def step(self):
        trash_cells = self.trash.select(self.trash.condition == 0)

        for robot in self.robots:
            for neighbor in self.area.neighbors(robot):
                if neighbor.condition == 0:
                    neighbor.condition = 2
                    break
            else:
                rand_move = random.choice(moves)
                self.area.move_by(robot, rand_move)
        
        #Termina simulacion
        if len(trash_cells) == 0:
            self.stop()

Simulación

In [65]:
parameters = {
    'height': 10,
    'length': 20,
    'Number of robots': 5,
    'density': 0.3,
    'steps': 200
}

In [67]:
def animation_plot(model, ax):
    attr_grid = model.area.attr_grid('condition')
    color_dict = {0:'#563939', 1:'#2758FF', 2:'#FFFFFF', None:'#FFFFFF'}
    ap.gridplot(attr_grid, ax=ax, color_dict=color_dict, convert=True)
    ax.set_title(f"Simulacion de Robots Limpiadores\n"
                 f"Time-step: {model.t}, Celda limpias: "
                 f"{len(model.agents.select(model.agents.condition == 2))}")

fig, ax = plt.subplots()
model = VacuumModel(parameters)
animation = ap.animate(model, fig, ax, animation_plot)
IPython.display.HTML(animation.to_jshtml(fps=15))